In [2]:
import numpy as np
import pandas as pd
from pathlib import Path

In [3]:
df = pd.read_csv(Path.cwd().parent / "data" / "spy_eod_202303.txt")

df

[QUOTE_UNIXTIME]   [QUOTE_READTIME]  [QUOTE_DATE]   [QUOTE_TIME_HOURS]  \
0            1677704400   2023-03-01 16:00    2023-03-01                 16.0   
1            1677704400   2023-03-01 16:00    2023-03-01                 16.0   
2            1677704400   2023-03-01 16:00    2023-03-01                 16.0   
3            1677704400   2023-03-01 16:00    2023-03-01                 16.0   
4            1677704400   2023-03-01 16:00    2023-03-01                 16.0   
...                 ...                ...           ...                  ...   
91230        1680292800   2023-03-31 16:00    2023-03-31                 16.0   
91231        1680292800   2023-03-31 16:00    2023-03-31                 16.0   
91232        1680292800   2023-03-31 16:00    2023-03-31                 16.0   
91233        1680292800   2023-03-31 16:00    2023-03-31                 16.0   
91234        1680292800   2023-03-31 16:00    2023-03-31                 16.0   

        [UNDERLYING_LAST]  [EXPIRE_DATE]   [EXPIRE_UNIX]   [DTE]   [C_DELTA]  \
0                  394.76     2023-03-01      1677704400    0.00     1.00000   
1                  394.76     2023-03-01      1677704400    0.00     1.00000   
2                  394.76     2023-03-01      1677704400    0.00     1.00000   
3                  394.76     2023-03-01      1677704400    0.00     1.00000   
4                  394.76     2023-03-01      1677704400    0.00     1.00000   
...                   ...            ...             ...     ...         ...   
91230              409.39     2025-12-19      1766178000  994.04     0.08235   
91231              409.39     2025-12-19      1766178000  994.04     0.08401   
91232              409.39     2025-12-19      1766178000  994.04     0.06465   
91233              409.39     2025-12-19      1766178000  994.04     0.07999   
91234              409.39     2025-12-19      1766178000  994.04     0.05785   

        [C_GAMMA]  ...   [P_LAST]   [P_DELTA]   [P_GAMMA]  [P_VEGA]  \
0         0.00000  ...       0.01    -0.00069     0.00008  -0.00004   
1         0.00000  ...       0.02    -0.00080     0.00011   0.00034   
2         0.00000  ...       0.00    -0.00075     0.00014   0.00100   
3         0.00000  ...       0.00    -0.00128     0.00020   0.00096   
4         0.00000  ...       0.00    -0.00050     0.00015   0.00027   
...           ...  ...        ...         ...         ...       ...   
91230     0.00152  ...       0.00    -1.00000     0.00000   0.00000   
91231     0.00146  ...       0.00    -1.00000     0.00000   0.00000   
91232     0.00132  ...       0.00    -1.00000     0.00000   0.00000   
91233     0.00138  ...       0.00    -1.00000     0.00000   0.00000   
91234     0.00116  ...     240.32    -1.00000     0.00000   0.00000   

       [P_THETA]   [P_RHO]     [P_IV]   [P_VOLUME]   [STRIKE_DISTANCE]  \
0       -0.00482   0.00000   1.486360     0.000000                74.8   
1       -0.00529   0.00000   1.282980     0.000000                64.8   
2       -0.00509  -0.00046   1.162910                             58.8   
3       -0.00470   0.00000   1.143500                             57.8   
4       -0.00523  -0.00017   1.123140                             56.8   
...          ...       ...        ...          ...                 ...   
91230    0.00000   0.00000                                       220.6   
91231    0.00000   0.00000                                       225.6   
91232    0.00000   0.00000                                       230.6   
91233    0.00000   0.00000                                       235.6   
91234    0.00000   0.00000                0.000000               240.6   

        [STRIKE_DISTANCE_PCT]  
0                       0.189  
1                       0.164  
2                       0.149  
3                       0.146  
4                       0.144  
...                       ...  
91230                   0.539  
91231                   0.551  
91232                   0.563  
91233      

In [7]:
df.columns = [k.strip(' ') for k in df.columns]
counts = df.groupby(['[QUOTE_UNIXTIME]', '[STRIKE]']).ngroups
counts_strikes = df.groupby(["[STRIKE]"]).ngroups
counts_exps = df.groupby(["[EXPIRE_DATE]"]).ngroups
counts_snapshot_times = df.groupby(["[QUOTE_UNIXTIME]"]).ngroups
print('counts:', counts) # amount of contracts in total (including calls/puts)
print('strike count:', counts_strikes)
print('exp counts:', counts_exps)
print('T:', counts_snapshot_times)

counts: 6642
strike count: 289
exp counts: 53
T: 23


In [38]:
import pandas as pd
import numpy as np

df = df.replace(' ', np.nan).replace('', np.nan)
df = df.fillna(0)
df.columns = df.columns.str.strip()

# Ensure numeric columns are converted to float
numeric_columns = ['[C_VOLUME]', '[P_VOLUME]', '[UNDERLYING_LAST]', '[STRIKE]']
for col in numeric_columns:
    df[col] = df[col].astype(float)

In [60]:
import plotly.graph_objects as go

fig = go.Figure()

groups = df.groupby(["[STRIKE]", "[EXPIRE_DATE]"])
groupnames = list(groups.groups.keys())
for gn in groupnames:
    group = groups.get_group(gn)
    subgr = group.groupby("[QUOTE_UNIXTIME]").agg({
        "[P_VOLUME]": "sum", "[C_VOLUME]": "sum"
        })
    sum_volumes = subgr["[P_VOLUME]"] + subgr["[C_VOLUME]"]
    fig.add_trace(go.Scatter(x=group["[QUOTE_READTIME]"], y=sum_volumes, name=str(gn), mode="markers"))


fig.show()